In [1]:
%matplotlib inline
import pandas as pd
import numpy as np
import seaborn as sns
import scipy
import operator
import gc

In [2]:
PATH = '../data/'

PROP_DATA_PATH = PATH + 'Property dataset/'
TRN_DATA_PATH = PATH + 'training dataset/'
TEST_DATA_PATH = PATH + 'Test dataset/'

In [3]:
##### Accounts Profiles

accounts_table = pd.read_csv(TRN_DATA_PATH+'Accounts.csv')

accounts_table.head()

accounts_table.describe()

accts_table_cnts_features = [
                                'active_deals',
                                'activity_count',
                                'num_deals_as_client',
                                'num_deals_as_investor',
                                'number_of_properties',
                                'number_of_related_deals',
                                'number_of_related_properties',
                                'number_of_won_deals_as_client'
                            ]

accts_table_bool_vars = [
                            'buyer_book',
                            'servicing_contract',
                            'cmbs',
                            'consultant',
                            'correspondent',
                            'foreign',
                            'master_servicer',
                            'lender_book',
                            'loan_sales_book',
                            'loan_servicing'
                        ]

for var in accts_table_bool_vars:
    print(accounts_table[var].value_counts())

for var in accts_table_bool_vars:
    accounts_table[var].replace([True,False],[1,0],inplace=True)

accounts_table.head()

accts_ids = accounts_table.id_accs.values.tolist()

accts_profiles = accounts_table[accts_table_cnts_features+accts_table_bool_vars].values.astype('float')

True     2189
False     567
Name: buyer_book, dtype: int64
False    2700
True       56
Name: servicing_contract, dtype: int64
False    2749
True        7
Name: cmbs, dtype: int64
False    2756
Name: consultant, dtype: int64
False    2741
True       15
Name: correspondent, dtype: int64
False    2578
True      178
Name: foreign, dtype: int64
False    2754
True        2
Name: master_servicer, dtype: int64
False    1509
True     1247
Name: lender_book, dtype: int64
True     1792
False     964
Name: loan_sales_book, dtype: int64
False    2755
True        1
Name: loan_servicing, dtype: int64


In [4]:
##### Properties profiles
property_data = pd.read_csv(PROP_DATA_PATH+'Properties.csv')
property_data.drop('id_deals',axis=1,inplace=True)
display(property_data.head())
property_data_cnt_feats = [
                            'price_per_sq_ft',
                            'num_buildings',
                            'num_floors',
                            'num_parking_spaces',
                            'sale_amount__c',
                            'size_sf',
                            'year_built'
                        ]

# features_to_impute = [
#                         'price_per_sq_ft',
#                         'num_buildings',
#                         'num_floors',
#                         'num_parking_spaces',
#                         'sale_amount__c',
#                         'size_sf',
#                         'year_built'
#                      ]

# for feat in property_data_cnt_feats:
#     temp = property_data.groupby(['city'])[feat].agg('mean').reset_index()
#     cities = temp['city'].values.tolist()
#     feat_means = temp[feat].values.tolist()
#     for ct in cities:
#         property_data.loc[property_data['city']==ct,feat] = temp.loc[temp['city']==ct][feat].values[0]

property_ids = property_data.id_props.values.tolist()

property_profiles = property_data[property_data_cnt_feats].fillna(0).values

def get_property_feature_vector(idx):
    property_feat_vec = property_profiles[idx]
    return property_feat_vec

def get_similar_accounts(acct_id):
    acct_id_idx = accts_ids.index(acct_id)
    acct_id_feature_vector = accts_profiles[acct_id_idx].astype('float')
    reccs = [(i,scipy.spatial.distance.cosine(acct_id_feature_vector,apf.astype('float')))\
             for i,apf in enumerate(accts_profiles)]
    reccs.sort(key=operator.itemgetter(1))
    return reccs

# array([2.22280e+02, 1.00000e+00, 2.00000e+00, 4.00000e+02, 2.25000e+07,
#        1.01223e+05, 2.00100e+03])

# array([4.29969e+03, 0.00000e+00, 0.00000e+00, 0.00000e+00, 8.00000e+07,
#        1.86060e+04, 2.00300e+03])

id_props building_status  \
0  a0I2A00000XQGKlUAP        Existing   
1  a0I2A00000XQGKnUAP             NaN   
2  a0I2A00000XQGKoUAP        Existing   
3  a0I2A00000XQGKpUAP             NaN   
4  a0I2A00000XQGKqUAP             NaN   

                               building_tax_expenses       city    class  \
0                                2009 Tax @ $1.25/sf  City-0488  Class B   
1                                                NaN  City-1975  Class A   
2  2016 Tax @ $5.63/sf; 2007 Ops @ $19.58/sf, 201...  City-1415  Class B   
3                                                NaN  City-1415  Class A   
4                                                NaN  City-0941      NaN   

        county sale_status  portfolio       market  num_buildings     ...      \
0  County-0172           N      False  Market-0059            1.0     ...       
1  County-0465           Y       True  Market-0239            NaN     ...       
2  County-0452           N      False  Market-0165            1.0     ...       
3  County-0452           N      False  Market-0165            1.0     ...       
4  County-0284           N      False  Market-0106            NaN     ...       

   price_per_sq_ft  price_per_unit  property_type_1  region__c  \
0            46.59     18350000.00       Industrial  Southwest   
1          1141.55      2109090.91    Multi-Housing  Southeast   
2          1506.65             NaN           Retail  Northeast   
3           580.83      1220689.66              NaN  Northeast   
4              NaN             NaN     Self-Storage  Southwest   

   sale_amount__c sale_date__c size_acres   size_sf size_units  year_built  
0    1.835000e+07    7/10/2015      3.760  393862.0        1.0      1980.0  
1    2.144058e+07   12/31/2016     19.600  508080.0      275.0      2014.0  
2    2.754156e+07    9/30/2016      0.266   18280.0        NaN      1902.0  
3    1.416000e+08    1/21/2016      0.530  243789.0      116.0         NaN  
4    0.000000e+00    9/30/2014        NaN       NaN        NaN         NaN  

[5 rows x 23 columns]

In [20]:
# opportunities_table = pd.read_csv(TRN_DATA_PATH+'Opportunities.csv')

# deal_to_properties_table = pd.read_csv(TRN_DATA_PATH+'Deals_to_Properties.csv')

In [6]:
##### Accounts profiling on the basis of Property Features

accounts_to_properties_table = pd.read_csv(TRN_DATA_PATH+'Accounts_properties.csv')
accounts_to_properties_table.drop('id_deals',axis=1,inplace=True)

d1 = pd.merge(accounts_to_properties_table,property_data,on=['id_props'],how='left')

# Define all the groupby transformations
GROUPBY_AGGREGATIONS = [
        {'groupby': ['id_accs'], 'select': 'price_per_sq_ft', 'agg': 'mean'},
        {'groupby': ['id_accs'], 'select': 'num_buildings', 'agg': 'mean'},
        {'groupby': ['id_accs'], 'select': 'num_floors', 'agg': 'mean'},
        {'groupby': ['id_accs'], 'select': 'num_parking_spaces', 'agg': 'mean'},
        {'groupby': ['id_accs'], 'select': 'sale_amount__c', 'agg': 'mean'},
        {'groupby': ['id_accs'], 'select': 'size_sf', 'agg': 'mean'},
        {'groupby': ['id_accs'], 'select': 'year_built', 'agg': 'mean'},
    ]

# Apply all the groupby transformations
for spec in GROUPBY_AGGREGATIONS:
    
    # Name of the aggregation we're applying
    agg_name = spec['agg_name'] if 'agg_name' in spec else spec['agg']
    
    # Name of new feature
    new_feature = '{}_{}_{}'.format('_'.join(spec['groupby']), agg_name, spec['select'])
    # print(new_feature)
    # Info
    print("Grouping by {}, and aggregating {} with {}".format(
        spec['groupby'], spec['select'], agg_name
    ))
    
    # Unique list of features to select
    all_features = list(set(spec['groupby'] + [spec['select']]))
    # print(all_features)
    # Perform the groupby
    gp = d1[all_features]. \
        groupby(spec['groupby'])[spec['select']]. \
        agg(spec['agg']). \
        reset_index(). \
        rename(index=str, columns={spec['select']: new_feature})
    # print(gp)
    d1 = d1.merge(gp, on=spec['groupby'], how='left')
     # Clear memory
    del gp
    gc.collect()

d11 = d1[
            [
                'id_accs',
                'id_accs_mean_price_per_sq_ft',
                'id_accs_mean_num_buildings',
                'id_accs_mean_num_floors',
                'id_accs_mean_num_parking_spaces',
                'id_accs_mean_sale_amount__c',
                'id_accs_mean_size_sf',
                'id_accs_mean_year_built'
            ]
        ]

d11_dash = d11.drop_duplicates()

acc_profiles_wrt_property_features = d11_dash.fillna(0).values[:,1:]

acc_profiles_wrt_property_features.shape

Grouping by ['id_accs'], and aggregating price_per_sq_ft with mean
Grouping by ['id_accs'], and aggregating num_buildings with mean
Grouping by ['id_accs'], and aggregating num_floors with mean
Grouping by ['id_accs'], and aggregating num_parking_spaces with mean
Grouping by ['id_accs'], and aggregating sale_amount__c with mean
Grouping by ['id_accs'], and aggregating size_sf with mean
Grouping by ['id_accs'], and aggregating year_built with mean


(2727, 7)

In [7]:
test_data = pd.read_csv(TEST_DATA_PATH+'Test_Data.csv')

test_data.head()

ids = list(test_data['id_accs'].values)

exclude = set(list(accounts_to_properties_table.id_props.unique()))

print(len(exclude))

63001


In [19]:
def filter_similar_accts(tuples_list):
    uniq = {}
    x = np.array([each[1] for each in tuples_list])
    p = np.percentile(x,1)
    print("accounts_percentile",p)
    for tl in tuples_list:
        if tl[1] not in uniq:
            uniq[tl[1]] = tl[0]     
        if tl[1] > p:
            break
    return uniq

# def filter_similar_accts_updated(tuples_list):
#     sa = []
#     x = np.array([each[1] for each in tuples_list])
#     p = np.percentile(x,0.5)
#     print("accounts_percentile",p)
#     sa = [tl[0] for tl in tuples_list if tl[1] <= p]
#     return sa

results = {}

for i,_id in enumerate(ids):
    most_similar_accts = get_similar_accounts(_id)
    print(len(most_similar_accts))
    filtered_most_similar_accts = filter_similar_accts(most_similar_accts)
    filtered_most_similar_accts = filtered_most_similar_accts.values()
#     filtered_most_similar_accts = filter_similar_accts_updated(most_similar_accts)
    print(len(filtered_most_similar_accts))
    print(filtered_most_similar_accts)
    top_reccs = []
    for most_similar_acct in filtered_most_similar_accts:
        if most_similar_acct > 2727:
            continue
        v1 = None
        v1 = acc_profiles_wrt_property_features[most_similar_acct].astype('float')
        reccs = []
        reccs = [(i,scipy.spatial.distance.cosine(v1,pf))\
                 if not np.isnan(scipy.spatial.distance.cosine(v1,pf)) else (i,0)
                 for i,pf in enumerate(property_profiles)]
        reccs.sort(key=operator.itemgetter(1))
        reccs = [r for r in reccs if r[1]>0]
        x = np.array([each[1] for each in reccs])
        if x.size==0:
            continue
        p = np.percentile(x,1)
        top_reccs.extend([property_ids[r[0]] for r in reccs if r[1]<=p])
    results[_id] = list(set(top_reccs)-exclude)
    print(len(results[_id]))

2756
accounts_percentile 8.414923586275158e-08
14
[79, 367, 1061, 426, 221, 1911, 2125, 1297, 1705, 1102, 1438, 1278, 29, 176]


/home/chandrashekhar/anaconda3/lib/python3.6/site-packages/scipy/spatial/distance.py:698: RuntimeWarning: invalid value encountered in double_scalars
  dist = 1.0 - uv / np.sqrt(uu * vv)


[(15929, 1.2534817628306882e-10), (3181, 3.505202794684692e-10), (7329, 3.505202794684692e-10), (3726, 4.084033111695362e-10), (11612, 4.084033111695362e-10), (14671, 4.084033111695362e-10), (16294, 4.0963143987937656e-10), (16326, 4.0963143987937656e-10), (2619, 8.223136616081206e-10), (12827, 8.223136616081206e-10), (2620, 1.1891981843703547e-09), (10181, 1.1891981843703547e-09), (3808, 1.2240015667686066e-09), (5355, 1.2240015667686066e-09), (6018, 1.2240015667686066e-09), (6019, 1.2240015667686066e-09), (7425, 1.2240015667686066e-09), (7703, 1.2240015667686066e-09), (7782, 1.2240015667686066e-09), (8880, 1.2240015667686066e-09), (10344, 1.2240015667686066e-09), (11026, 1.2240015667686066e-09), (12045, 1.2240015667686066e-09), (12218, 1.2240015667686066e-09), (14189, 1.2240015667686066e-09), (16706, 1.2240015667686066e-09), (17561, 1.2240015667686066e-09), (1032, 1.39797717846335e-09), (1622, 1.39797717846335e-09), (2027, 1.39797717846335e-09), (2044, 1.39797717846335e-09), (3593, 1

[(54, 1.4674951254178836e-09), (1404, 1.4674951254178836e-09), (2526, 1.4674951254178836e-09), (2839, 1.4674951254178836e-09), (2843, 1.4674951254178836e-09), (2920, 1.4674951254178836e-09), (3008, 1.4674951254178836e-09), (3765, 1.4674951254178836e-09), (4173, 1.4674951254178836e-09), (4553, 1.4674951254178836e-09), (5120, 1.4674951254178836e-09), (5121, 1.4674951254178836e-09), (5296, 1.4674951254178836e-09), (5305, 1.4674951254178836e-09), (5699, 1.4674951254178836e-09), (5727, 1.4674951254178836e-09), (7841, 1.4674951254178836e-09), (10310, 1.4674951254178836e-09), (11581, 1.4674951254178836e-09), (12086, 1.4674951254178836e-09), (12295, 1.4674951254178836e-09), (13203, 1.4674951254178836e-09), (13540, 1.4674951254178836e-09), (13809, 1.4674951254178836e-09), (15393, 1.4674951254178836e-09), (16993, 1.4674951254178836e-09), (17000, 1.4674951254178836e-09), (3808, 4.5949316573867804e-09), (5355, 4.5949316573867804e-09), (6018, 4.5949316573867804e-09), (6019, 4.5949316573867804e-09),

[(2281, 1.1849643488659467e-10), (2851, 1.1849643488659467e-10), (4024, 1.1849643488659467e-10), (4644, 1.1849643488659467e-10), (6563, 1.1849643488659467e-10), (7407, 1.1849643488659467e-10), (7807, 1.1849643488659467e-10), (8758, 1.1849643488659467e-10), (8832, 1.1849643488659467e-10), (12776, 1.1849643488659467e-10), (1740, 1.2712737529341211e-09), (1787, 1.2712737529341211e-09), (2621, 1.2712737529341211e-09), (3079, 1.2712737529341211e-09), (3589, 1.2712737529341211e-09), (4263, 1.2712737529341211e-09), (5348, 1.2712737529341211e-09), (5479, 1.2712737529341211e-09), (5609, 1.2712737529341211e-09), (7532, 1.2712737529341211e-09), (11253, 1.2712737529341211e-09), (16185, 1.2712737529341211e-09), (16235, 1.2712737529341211e-09), (16696, 1.2712737529341211e-09), (16699, 1.2712737529341211e-09), (17372, 1.2712737529341211e-09), (17580, 1.2712737529341211e-09), (17827, 1.2712737529341211e-09), (18055, 1.2712737529341211e-09), (6216, 1.2720750008909931e-09), (9634, 1.2720750008909931e-09

...

[(175, 3.771917556072424e-09), (615, 3.771917556072424e-09), (881, 3.771917556072424e-09), (900, 3.771917556072424e-09), (995, 3.771917556072424e-09), (1045, 3.771917556072424e-09), (1122, 3.771917556072424e-09), (1148, 3.771917556072424e-09), (1556, 3.771917556072424e-09), (1718, 3.771917556072424e-09), (1793, 3.771917556072424e-09), (1881, 3.771917556072424e-09), (1909, 3.771917556072424e-09), (1996, 3.771917556072424e-09), (2124, 3.771917556072424e-09), (2157, 3.771917556072424e-09), (2162, 3.771917556072424e-09), (2218, 3.771917556072424e-09), (2283, 3.771917556072424e-09), (2357, 3.771917556072424e-09), (2515, 3.771917556072424e-09), (2540, 3.771917556072424e-09), (2655, 3.771917556072424e-09), (2768, 3.771917556072424e-09), (3068, 3.771917556072424e-09), (3078, 3.771917556072424e-09), (3160, 3.771917556072424e-09), (3196, 3.771917556072424e-09), (3233, 3.771917556072424e-09), (3239, 3.771917556072424e-09), (3285, 3.771917556072424e-09), (3286, 3.771917556072424e-09), (3488, 3.771

[(4337, 3.73584718715847e-10), (7268, 3.73584718715847e-10), (7535, 3.73584718715847e-10), (11771, 3.73584718715847e-10), (2448, 4.596815150748057e-10), (4, 1.0415718287859477e-09), (597, 1.0415718287859477e-09), (844, 1.0415718287859477e-09), (959, 1.0415718287859477e-09), (2567, 1.0415718287859477e-09), (3970, 1.0415718287859477e-09), (5086, 1.0415718287859477e-09), (5605, 1.0415718287859477e-09), (6703, 1.0415718287859477e-09), (6892, 1.0415718287859477e-09), (7099, 1.0415718287859477e-09), (7438, 1.0415718287859477e-09), (8157, 1.0415718287859477e-09), (8389, 1.0415718287859477e-09), (10034, 1.0415718287859477e-09), (10352, 1.0415718287859477e-09), (10860, 1.0415718287859477e-09), (10926, 1.0415718287859477e-09), (11041, 1.0415718287859477e-09), (11049, 1.0415718287859477e-09), (12202, 1.0415718287859477e-09), (12600, 1.0415718287859477e-09), (13356, 1.0415718287859477e-09), (15068, 1.0415718287859477e-09), (15472, 1.0415718287859477e-09), (4857, 1.0789795723553652e-09), (5583, 1.0

[(5662, 2.935538478965327e-10), (6351, 2.935538478965327e-10), (8161, 2.935538478965327e-10), (9515, 2.935538478965327e-10), (12606, 2.935538478965327e-10), (12642, 2.935538478965327e-10), (12913, 2.935538478965327e-10), (12950, 2.935538478965327e-10), (16254, 2.935538478965327e-10), (16902, 2.935538478965327e-10), (389, 3.1256075505581293e-10), (6894, 3.1256075505581293e-10), (11786, 3.1256075505581293e-10), (13541, 3.1256075505581293e-10), (15293, 3.1256075505581293e-10), (5592, 3.847119289801526e-10), (9417, 3.847119289801526e-10), (12011, 3.847119289801526e-10), (2268, 4.2285963619548284e-10), (4063, 4.2285963619548284e-10), (4773, 4.2285963619548284e-10), (6166, 4.2285963619548284e-10), (11251, 4.2285963619548284e-10), (14157, 4.2285963619548284e-10), (14845, 4.2285963619548284e-10), (2974, 4.355197313898884e-10), (4058, 4.355197313898884e-10), (5624, 4.355197313898884e-10), (11211, 4.355197313898884e-10), (11408, 4.355197313898884e-10), (979, 4.771864015040705e-10), (4468, 6.2143

[(3456, 2.717846692146253e-08), (15694, 2.717846692146253e-08), (16378, 2.717846692146253e-08), (48, 3.979022233924212e-08), (709, 3.979022233924212e-08), (710, 3.979022233924212e-08), (711, 3.979022233924212e-08), (712, 3.979022233924212e-08), (924, 3.979022233924212e-08), (962, 3.979022233924212e-08), (1055, 3.979022233924212e-08), (1085, 3.979022233924212e-08), (1094, 3.979022233924212e-08), (1216, 3.979022233924212e-08), (1552, 3.979022233924212e-08), (1663, 3.979022233924212e-08), (1664, 3.979022233924212e-08), (1665, 3.979022233924212e-08), (1666, 3.979022233924212e-08), (1705, 3.979022233924212e-08), (1725, 3.979022233924212e-08), (1745, 3.979022233924212e-08), (1966, 3.979022233924212e-08), (2061, 3.979022233924212e-08), (2191, 3.979022233924212e-08), (2338, 3.979022233924212e-08), (2356, 3.979022233924212e-08), (2623, 3.979022233924212e-08), (2775, 3.979022233924212e-08), (2794, 3.979022233924212e-08), (2822, 3.979022233924212e-08), (2823, 3.979022233924212e-08), (2941, 3.9790

[(3651, 1.6718062489928798e-09), (5942, 1.6718062489928798e-09), (6252, 1.6718062489928798e-09), (8005, 1.6718062489928798e-09), (8200, 1.6718062489928798e-09), (8638, 1.6718062489928798e-09), (10210, 1.6718062489928798e-09), (16033, 1.6718062489928798e-09), (1504, 3.944274573619566e-09), (5576, 3.944274573619566e-09), (6417, 3.944274573619566e-09), (8079, 3.944274573619566e-09), (9980, 3.944274573619566e-09), (11540, 3.944274573619566e-09), (15233, 3.944274573619566e-09), (15409, 3.944274573619566e-09), (15729, 3.944274573619566e-09), (16442, 3.944274573619566e-09), (16663, 3.944274573619566e-09), (17467, 3.944274573619566e-09), (237, 1.3692785350016834e-08), (277, 1.3692785350016834e-08), (443, 1.3692785350016834e-08), (475, 1.3692785350016834e-08), (590, 1.3692785350016834e-08), (642, 1.3692785350016834e-08), (765, 1.3692785350016834e-08), (884, 1.3692785350016834e-08), (1041, 1.3692785350016834e-08), (1092, 1.3692785350016834e-08), (1453, 1.3692785350016834e-08), (1698, 1.369278535

In [15]:
import csv
with open('subm13.csv','w') as fout:
    writer = csv.writer(fout)
    writer.writerow(['id_accs','id_prop'])
    for resid,res in results.items():
        for r in res:
            row = [resid]+[r]
            writer.writerow(row)